In [2]:
import plotly.graph_objects as go

import glob
import os
from tqdm import tqdm

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import seaborn as sns

pd.options.mode.chained_assignment = None  # default='warn'

import paths
import event_identification_tools
import fluxnet_tools
import pickle

In [3]:
if paths.USER == 'ericamcc':
    computer = 'DESKTOP'
else:
    computer = 'LAPTOP'
print(f"User path is set for the {computer}; paths.USER = {paths.USER}")

User path is set for the DESKTOP; paths.USER = ericamcc


# List of sites with questionable SWC

In [5]:
swc_sites_previously_inspected = [
'BE-Vie',  # jumps from low to high around 2007
'CA-NS2', # bad starting at end of 2004
'CA-NS4', # bad at very end of timeseries (2005-10)
'CA-SF1', # all data looks 'blocky' but the patterns seem okay. At low SWC it seems esp suspicious
'CA-SF2', # same as bove, but def bad data around beginning 2002
'CH-Lae', # all data might be good, but check 2013
'CN-Cha', # all data might be good, but check 2004-04ish
'DE-Lkb', # blocky in general, end of timeseries (2013-07) def bad
'DE-Lnf', # bad from 2007 to 2020
'DK-Sor', # bad from 2007 to 2013
'Fl-Sod', # possibly tiny bit of bad data at beginning of 2002
'IT-CA1', # possibly bad right at beginning of timeseries
'IT-Col', # bad during beginning from 2010-2011 ish
'IT-Cp2', # can't tell if beginning of high SWC (2012-07 to 2012-09) is bad or just weird
'IT-Ro1', # small bit of bad data at beginning of 2006 and end of 2007/beginning 2008
'JP-SMF', # 2004-07
'NL-Loo', # 2001-2002ish
'RU-Fyo', # lots of bad data: 2007 to 2009 and 2013ish on are bad
'US-Blo', # part of 1998 is bad and part of 199 is bad (could just cut pre 2000)
'US-SRC', # posibly bad high SWC data towards end of 2012
'US-Ton', # miiiight be bad data righ tat beginnign of 2006 (high SWC)
]

In [ ]:
swc_sites_to_inspect = [
    
]

## Make dataframe with all SWC data for all sites

In [6]:
# To visualize all sites, see below. Otherwise, use list from above.
# with open(paths.PATH_TO_SWC_SITES, 'rb') as fp:
#    site_list = pickle.load(fp)

site_list = swc_sites_to_inspect
df = pd.DataFrame()

for file in tqdm(glob.glob(paths.FLUXNET_DD_DIR + '/*')):
    site_name = file.split('/')[9][0:6] 
    if site_name in site_list:
        day_file = paths.FLUXNET_DD_DIR + '/' + site_name + '.csv'
        df_day = pd.read_csv(day_file, usecols = ['TIMESTAMP', 'SWC_F_MDS_1'], parse_dates = ['TIMESTAMP'], index_col = 'TIMESTAMP')
        df_day['SWC_cleaned'] = df_day['SWC_F_MDS_1'].replace(-9999, np.nan).dropna(axis = 0)
        
        df_day['site'] = site_name
        df_day['TIMESTAMP'] = df_day.index

        df = pd.concat([df, df_day])

df.head()


100%|██████████| 89/89 [00:00<00:00, 147.17it/s]


SWC_F_MDS_1  SWC_cleaned    site  TIMESTAMP
TIMESTAMP                                              
2003-01-01         11.3         11.3  CN-Cha 2003-01-01
2003-01-02         11.2         11.2  CN-Cha 2003-01-02
2003-01-03         11.2         11.2  CN-Cha 2003-01-03
2003-01-04         11.1         11.1  CN-Cha 2003-01-04
2003-01-05         10.9         10.9  CN-Cha 2003-01-05

In [7]:
buttons = []
i = 0

fig3 = go.Figure()

for site in site_list:
    fig3.add_trace(
        go.Scatter(
            x = df['TIMESTAMP'][df['site']==site],
            y = df['SWC_cleaned'][df['site']==site],
            name = site, visible = (i==0)
        )
    )
    
for site in site_list:
    args = [False] * len(site_list)
    args[i] = True
    
    #create a button object for the country we are on
    button = dict(label = site,
                  method = "update",
                  args=[{"visible": args}])
    
    #add the button to our list of buttons
    buttons.append(button)
    
    #i is an iterable used to tell our "args" list which value to set to True
    i+=1
    
fig3.update_layout(updatemenus=[dict(active=0,
                                    type="dropdown",
                                    buttons=buttons,
                                    x = 0,
                                    y = 1.1,
                                    xanchor = 'left',
                                    yanchor = 'bottom'),
                              ])

fig3.update_layout(xaxis1_rangeslider_visible=True,
                  height=600)

fig3.update_layout(
    autosize=False,
    width=1400,
    height=900,)


ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'name': 'BE-Vie',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(1996, 1, 1, 0, 0),
                          datetime.datetime(1996, 1, 2, 0, 0),
                          datetime.datetime(1996, 1, 3, 0, 0), ...,
                          datetime.datetime(2014, 12, 29, 0, 0),
                          datetime.datetime(2014, 12, 30, 0, 0),
                          datetime.datetime(2014, 12, 31, 0, 0)], dtype=object),
              'y': array([   nan,    nan,    nan, ..., 27.796, 27.702, 27.882])},
             {'name': 'CA-NS2',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(2001, 1, 1, 0, 0),
                          datetime.datetime(2001, 1, 2, 0, 0),
                          datetime.datetime(2001, 1, 3, 0, 0), ...,
                          datetime.datetime(2005, 12, 29, 0, 0),
                          datetime.datetime(2005, 12, 30, 0, 0),
                          datetime.datetime(2005, 12, 31, 0, 0)], dtype=object),
              'y': array([nan, nan, nan, ..., nan, nan, nan])},
             {'name': 'CA-NS4',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(2002, 1, 1, 0, 0),
                          datetime.datetime(2002, 1, 2, 0, 0),
                          datetime.datetime(2002, 1, 3, 0, 0), ...,
                          datetime.datetime(2005, 12, 29, 0, 0),
                          datetime.datetime(2005, 12, 30, 0, 0),
                          datetime.datetime(2005, 12, 31, 0, 0)], dtype=object),
              'y': array([nan, nan, nan, ..., nan, nan, nan])},
             {'name': 'CA-SF1',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(2003, 1, 1, 0, 0),
                          datetime.datetime(2003, 1, 2, 0, 0),
                          datetime.datetime(2003, 1, 3, 0, 0), ...,
                          datetime.datetime(2006, 12, 29, 0, 0),
                          datetime.datetime(2006, 12, 30, 0, 0),
                          datetime.datetime(2006, 12, 31, 0, 0)], dtype=object),
              'y': array([nan, nan, nan, ..., nan, nan, nan])},
             {'name': 'CA-SF2',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(2001, 1, 1, 0, 0),
                          datetime.datetime(2001, 1, 2, 0, 0),
                          datetime.datetime(2001, 1, 3, 0, 0), ...,
                          datetime.datetime(2005, 12, 29, 0, 0),
                          datetime.datetime(2005, 12, 30, 0, 0),
                          datetime.datetime(2005, 12, 31, 0, 0)], dtype=object),
              'y': array([nan, nan, nan, ..., nan, nan, nan])},
             {'name': 'CH-Lae',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(2004, 1, 1, 0, 0),
                          datetime.datetime(2004, 1, 2, 0, 0),
                          datetime.datetime(2004, 1, 3, 0, 0), ...,
                          datetime.datetime(2014, 12, 29, 0, 0),
                          datetime.datetime(2014, 12, 30, 0, 0),
                          datetime.datetime(2014, 12, 31, 0, 0)], dtype=object),
              'y': array([   nan,    nan,    nan, ..., 24.356, 24.277, 24.354])},
             {'name': 'CN-Cha',
              'type': 'scatter',
              'visible': True,
              'x': array([datetime.datetime(2003, 1, 1, 0, 0),
                          datetime.datetime(2003, 1, 2, 0, 0),
                          datetime.datetime(2003, 1, 3, 0, 0), ...,
                          datetime.datetime(2005, 12, 29, 0, 0),
                          datetime.datetime(2005, 12, 30, 0, 0),
                          datetime.datetime(2005, 12, 31, 0, 0)], dtype=object),
              'y': array([11.3, 11.2, 11.2, ...,  8.6,  8.8,  8.